In [ ]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import time
import os
import random
from concurrent.futures import ThreadPoolExecutor, as_completed
DataSet  = pd.read_csv('../Data/CleanData.csv')

In [10]:
list_url = DataSet['url'].tolist()


In [23]:
i = 0
years = []
user_agents = [
    'Mozilla/5.0 (Windows NT 10.0; Win64; x64)...',
    'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7)...',
    'Mozilla/5.0 (X11; Linux x86_64)...',
    'Mozilla/5.0 (iPhone; CPU iPhone OS 14_0 like Mac OS X)...',
    'Mozilla/5.0 (Windows NT 10.0; Win64; x64)... Safari/537.36',
]
def get_headers():
    return {
        'User-Agent': random.choice(user_agents)
    }

def fetch_with_retries(url, params=None):
    for attempt in range(5):
        try:
            response = requests.get(url, headers=get_headers() ,  params=params, timeout=2)
            if response.status_code == 200 and "captcha" not in response.text.lower():
                return response
            else:
                print(f"[!] Retry {attempt+1} - Status: {response.status_code}")
                time.sleep(random.uniform(2, 5))
        except Exception as e:
            print(f"[!] Error fetching {url}: {e}")
            time.sleep(random.uniform(2, 4))
    return None

for url in list_url: 
      print(url)
      year = None
      try : 
          response = fetch_with_retries(url)
          if  response:
              soup = BeautifulSoup(response.text , 'html.parser')
              features_divs = soup.find_all('div', {'class': 'dnArJl'})
              values = labels = []
              if len(features_divs) >= 1: 
                    year = features_divs[0].find_all('span', {'class': 'fjZBup'})[0].text

       
      
      except Exception as e : 
        print(f"[!] Error scraping car {url}: {str(e)}")
      years.append(year)
      print("index" , i  , "year" , year)
      i += 1
        

https://www.avito.ma/fr/2_mars/voitures_d'occasion/Opel_adam_1er_main_55731615.htm
index 0 year 2010
https://www.avito.ma/fr/anfa/voitures_d'occasion/Dacia_Duster_Diesel_Manuelle_2022_à_Casablanca_56009189.htm
index 1 year 2021
https://www.avito.ma/fr/2_mars/voitures_d'occasion/Glof_7_diesel_automatique__54985830.htm
index 2 year 2021
https://www.avito.ma/fr/anfa/voitures_d'occasion/toyota_corolla_56205782.htm
index 3 year None
https://www.avito.ma/fr/yacoub_el_mansour/voitures_d'occasion/Volkswagen_Golf_2_Diesel_Manuelle_1987_à_Rabat_56256157.htm
index 4 year 1987
https://www.avito.ma/fr/al_hoceima/voitures_d'occasion/Mercedes_Benz_GLB_220d_AMG_Line_4Matic_56297844.htm
index 5 year 2021
https://www.avito.ma/fr/administratif/voitures_d'occasion/Dacia_Dokker_Diesel_Manuelle_2018_à_Tanger_56297845.htm
index 6 year None
https://www.avito.ma/fr/bournazil/voitures_d'occasion/Honda_CR_V_Diesel_Automatique_2014_à_Casablanca_56202006.htm
index 7 year 2014
https://www.avito.ma/fr/khénifra/voitu

KeyboardInterrupt: 

In [25]:
print(len(DataSet))

64333


In [ ]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import time
import os
import random
from concurrent.futures import ThreadPoolExecutor, as_completed

# ----------------------------------------
# Config
# ----------------------------------------

base_url = 'https://www.avito.ma/fr/maroc/voitures'
output_file = 'avito_cars_data.csv'
max_pages = 2609
max_threads = 10
retry_limit = 3

# ----------------------------------------
# Headers Rotation
# ----------------------------------------

user_agents = [
    'Mozilla/5.0 (Windows NT 10.0; Win64; x64)...',
    'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7)...',
    'Mozilla/5.0 (X11; Linux x86_64)...',
    'Mozilla/5.0 (iPhone; CPU iPhone OS 14_0 like Mac OS X)...',
    'Mozilla/5.0 (Windows NT 10.0; Win64; x64)... Safari/537.36',
]

def get_headers():
    return {
        'User-Agent': random.choice(user_agents)
    }

# ----------------------------------------
# CSV Setup
# ----------------------------------------

if not os.path.exists(output_file):
    pd.DataFrame(columns=[
        'url', 'year'  , 'type_boit', 'type_carburant',
        'kilometrage', 'marke', 'model',
        'puissance', 'price' , 
        'has_abs' ,'has_airbags' , 'has_bluetooth_audio' ,'has_rear_camera' , 'has_ac' , 'has_esp'
          , 'has_alloy_wheels' , 'has_speed_limiter' , 'has_trip_computer' ,'has_parking_sensor' , 
          'has_cruise_control' , 'has_leather_seats' , 'has_gps',  'has_sunroof' , 'has_remote_locking'
          ,'has_power_windows' 
    ]).to_csv(output_file, index=False)

# ----------------------------------------
# Safe Request with Retry
# ----------------------------------------

def fetch_with_retries(url, params=None):
    for attempt in range(retry_limit):
        try:
            response = requests.get(url, headers=get_headers(), params=params, timeout=10)
            if response.status_code == 200 and "captcha" not in response.text.lower():
                return response
            else:
                print(f"[!] Retry {attempt+1} - Status: {response.status_code}")
                time.sleep(random.uniform(2, 5))
        except Exception as e:
            print(f"[!] Error fetching {url}: {e}")
            time.sleep(random.uniform(2, 4))
    return None

# ----------------------------------------
# Car Detail Scraper
# ----------------------------------------
def scrape_car(url):
    try:
        if not url.startswith("http"):
            url = "https://www.avito.ma" + url

        response = fetch_with_retries(url)
        if not response:
            return None

        soup = BeautifulSoup(response.text, 'html.parser')

        # --- PRICE ---
        price_tag = soup.find('p', {'class': 'jdRkSM'})
        price = price_tag.text.strip() if price_tag else None

        # --- BASIC FEATURES (first div.dnArJl) ---
        features_divs = soup.find_all('div', {'class': 'dnArJl'})
        values = labels = []
        if len(features_divs) >= 1:
            values = features_divs[0].find_all('span', {'class': 'fjZBup'})
            labels = [s.text.strip() for s in features_divs[0].find_all('span', {'class': 'bXFCIH'})]
        get = lambda i: values[i].text.strip() if len(values) > i else None

        get_by_label = lambda name: get(labels.index(name)) if name in labels else None

        # --- Feature Mapping (renamed columns) ---
        real_features = {
            'ABS': 'has_abs',
            'Airbags': 'has_airbags',
            'CD/MP3/Bluetooth': 'has_bluetooth_audio',
            'Caméra de recul': 'has_rear_camera',
            'Climatisation': 'has_ac',
            'ESP': 'has_esp',
            'Jantes aluminium': 'has_alloy_wheels',
            'Limiteur de vitesse': 'has_speed_limiter',
            'Ordinateur de bord': 'has_trip_computer',
            'Radar de recul': 'has_parking_sensor',
            'Régulateur de vitesse': 'has_cruise_control',
            'Sièges cuir': 'has_leather_seats',
            'Système de navigation/GPS': 'has_gps',
            'Toit ouvrant': 'has_sunroof',
            'Verrouillage centralisé à distance': 'has_remote_locking',
            'Vitres électriques': 'has_power_windows'
        }

        # --- EXTRA FEATURES (second div.dnArJl) ---
        feature_status = {new_key: 0 for new_key in real_features.values()}  # default to 0
        if len(features_divs) >= 2:
            feature_texts = [
                span.text.strip() for span in features_divs[1].find_all('span', {'class': 'fjZBup'})
            ]
            feature_status = {
                new_key: 1 if old_key in feature_texts else 0
                for old_key, new_key in real_features.items()
            }

        # --- Final Data Dictionary ---
        return {
            'url': url,
            'year' : get(0) , 
            'type_boit': get(1),
            'type_carburant': get(2),
            'kilometrage': get(3),
            'marke': get(4),
            'model': get(5),
            'puissance': get_by_label('Puissance fiscale'),
            **feature_status , 
            'price': price
            
        }

    except Exception as e:
        print(f"[!] Error scraping car {url}: {str(e)}")
        return None


for page in range(1500, 1800+1):
    print(f"\n🌐 Scraping page {page}...")
    params = {'o': page}
    car_links = []

    response = fetch_with_retries(base_url, params=params)
    if response:
        soup = BeautifulSoup(response.text, 'html.parser')
        container = soup.find('div', {'class': 'crKvIr'})
        if container:
            links = container.find_all('a', {'class': 'jZXrfL'})
            car_links = [link['href'] for link in links if link.get('href')]
            print(f"[+] Found {len(car_links)} cars on page {page}")
        else:
            print("[!] No container found on this page")
    else:
        print(f"[!] Failed to fetch page {page}, skipping.")
        continue

    page_data = []
    with ThreadPoolExecutor(max_workers=max_threads) as executor:
        futures = [executor.submit(scrape_car, url) for url in car_links]
        for future in as_completed(futures):
            result = future.result()
            if result:
                page_data.append(result)

    # Save after each page
    if page_data:
        pd.DataFrame(page_data).to_csv(output_file, mode='a', header=False, index=False)
        print(f"✅ Saved {len(page_data)} cars from page {page}")
    else:
        print(f"⚠️ No data to save for page {page}")

    # Random polite delay
    if page % 20 == 0:
        print("😴 Taking longer break...")
        time.sleep(random.uniform(10, 20))
    else:
        time.sleep(random.uniform(2, 4))

print("\n🎉 Done scraping all pages!")



🌐 Scraping page 1500...
[+] Found 35 cars on page 1500
[!] Retry 1 - Status: 511
✅ Saved 35 cars from page 1500
😴 Taking longer break...

🌐 Scraping page 1501...
[+] Found 35 cars on page 1501
✅ Saved 35 cars from page 1501

🌐 Scraping page 1502...
[+] Found 35 cars on page 1502
[!] Retry 1 - Status: 511
✅ Saved 35 cars from page 1502

🌐 Scraping page 1503...
[+] Found 35 cars on page 1503
✅ Saved 35 cars from page 1503

🌐 Scraping page 1504...
[+] Found 35 cars on page 1504
[!] Error fetching https://www.avito.ma/fr/hay_mohammadi/voitures_d'occasion/touran_Volkswagen__55663292.htm: HTTPSConnectionPool(host='www.avito.ma', port=443): Read timed out.
✅ Saved 35 cars from page 1504

🌐 Scraping page 1505...
[+] Found 35 cars on page 1505
✅ Saved 35 cars from page 1505

🌐 Scraping page 1506...
[+] Found 35 cars on page 1506
[!] Retry 1 - Status: 511
✅ Saved 35 cars from page 1506

🌐 Scraping page 1507...
[+] Found 35 cars on page 1507
✅ Saved 35 cars from page 1507

🌐 Scraping page 1508..

In [30]:
data = pd.read_csv('avito_cars.csv')
print(data.tail()['url'].tolist())

['https://www.avito.ma/fr/ksar_es_seghir/voitures_de_location/citroen_c_elysee_56188239.htm', "https://www.avito.ma/fr/ain_harrouda/voitures_d'occasion/Ford_Fiesta_diwana_56110130.htm", "https://www.avito.ma/fr/centre/voitures_d'occasion/Mercedes_Benz_250_Diesel_Automatique_2015_56317656.htm", "https://www.avito.ma/fr/ain_sebaa/voitures_d'occasion/Dacia_logan_Essence_4cylindres_Essence__56317655.htm", "https://www.avito.ma/fr/ain_sebaa/voitures_d'occasion/Mercedes_Benz_GLE_300_d_4MATIC_Luxury_56171842.htm"]


In [32]:
print(data.tail())

                                                  url  type_boit  \
63  https://www.avito.ma/fr/ksar_es_seghir/voiture...        NaN   
64  https://www.avito.ma/fr/ain_harrouda/voitures_...     2008.0   
65  https://www.avito.ma/fr/centre/voitures_d'occa...     2015.0   
66  https://www.avito.ma/fr/ain_sebaa/voitures_d'o...     2019.0   
67  https://www.avito.ma/fr/ain_sebaa/voitures_d'o...     2020.0   

   type_carburant kilometrage              marke          model        year  \
63            NaN         NaN                NaN            NaN         NaN   
64       Manuelle      Diesel  200 000 - 249 999           Ford      Fiesta   
65    Automatique      Diesel    25 000 - 29 999  Mercedes-Benz         250   
66       Manuelle     Essence  130 000 - 139 999          Dacia       Logan   
67    Automatique      Diesel    70 000 - 74 999  Mercedes-Benz  Classe GLE   

   puissance  price  has_abs  ...  has_alloy_wheels  has_speed_limiter  \
63       NaN      0        0  ...         